# CS 201: Tail Recursion
<p>
<script language="JavaScript">
    document.write("Last modified: " + document.lastModified)
</script>

In [43]:
(require racket)
(require racket/base)

### Defining local variables with let and let*


<code>let</code> creates local variables within your procedure.
It does not pollute the global namespace. Below we create two local variables, <tt>y</tt> and <tt>z</tt>.

In [44]:
(define (f x)
  (let ((y (* x 2 ))
        (z (+ x 2)))
    (list x y z)))

In [45]:
(f 10)

'(10 20 12)

<code>let*</code> is like <code>let</code>, but you can refer to other local variables within <code>let*</code>.

In [46]:
(define (g x)
  (let* ((y (* x 2)) 
         (z (+ y 2)))
    (list x y z)))

In [47]:
(g 10)

'(10 20 22)

This is what you would need to do if you did not have <code>let*</code>.

In [48]:
(define (h x)
  (let ((y (* x 2)))
    (let ((z (+ y 2)))
      (list x y z))))

In [49]:
(h 10)

'(10 20 22)

## Defining Functions with Optional Arguments

Below we define a function <tt>size</tt> which returns the size of an object.  By default, it uses <tt>length</tt> as the measure of size, but you can specify another function to specify the size.  Note the dot notation to specify the optional argument <tt>proc</tt>

In [50]:
(define (size lst . proc)
  (let ((func (if (null? proc)
                  length
                  (car proc))))
    (func lst)))

In [51]:
(size '(1 2 3 4 5 2))

6

In [52]:
(size '(1 2 3 4 2) max)

max: contract violation
  expected: real?
  given: '(1 2 3 4 2)


In [53]:
(max 1 2 3)

3

The problem is that <code>max</code> unlike <code>length</code> takes a variable number of arguments, not a single list.

In [54]:
(size '(1 2 3 4 2) (lambda (x) (apply max x)))

4

We can use square brackets to specify the default value for an optional argument: <code>[optional-arg default-value]</code>

In [55]:
(define (size2 lst [proc length])
  (proc lst))

In [56]:
(size2 '(1 2 8 4 5 2))

6

In [57]:
(size2 '(1 2 8 4 5) max)

max: contract violation
  expected: real?
  given: '(1 2 8 4 5)


In [58]:
(size2 '(1 2 8 4 5) (lambda (x) (apply max x)))

8

### Recursive Integer Operations

We define the following functions:
- <tt>last-digit</tt> return the low order decimal digit of an integer
- <tt>split</tt> break an integer into a list of decimal digits
- <tt>join</tt> convert a list of decimal digits into an integer

In [59]:
(define d 736241)
(define x '(7 3 6 2 4 1))

In [60]:
(define (last-digit n)
  (abs (remainder n 10)))

In [61]:
(last-digit d)

1

In [62]:
(last-digit -1236337373)

3

In [63]:
(define (split n)
  (reverse (split-aux n)))

(define (split-aux n)
  (if (< n 10)
      (cons n '())
      (cons (last-digit n) (split-aux (quotient n 10)))))

In [64]:
(split d)

'(7 3 6 2 4 1)

In [65]:
(split-aux d)

'(1 4 2 6 3 7)

In [66]:
(define (join lst)
  (join-aux lst 0))

(define (join-aux lst num)
  (if (null? lst)
      num
      (join-aux (cdr lst) (+ (car lst) (* 10 num)))))

In [67]:
(join x)

736241

In [68]:
(join (split d))

736241

Note that both <tt>split</tt> and <tt>join</tt> used an auxiliary function to implement the recursion.  We can write <tt>join</tt> without a helper function by using a default parameter for the initial result.

In [69]:
(define (join2 lst [num 0])
  (if (null? lst)
      num
      (join2 (cdr lst) (+ (car lst) (* 10 num)))))

In [70]:
(join2 x)

736241

In [71]:
(join2 (split d))

736241

<h3 id="append">More Recursion: append and replicate</h3>

<tt>append</tt> splices together two lists. Note that <tt>cons</tt> is slightly different.  We can define <tt>my-append</tt> using recursion.

In [72]:
(append '(1 2 3) '(4 5 6))

'(1 2 3 4 5 6)

In [73]:
(cons '(1 2 3) '(4 5 6))

'((1 2 3) 4 5 6)

In [74]:
(define (my-append list1 list2)
  (if (null? list1) list2
      (cons (car list1) (my-append (cdr list1) list2))))

In [75]:
(my-append '(1 2 3) '(4 5 6))

'(1 2 3 4 5 6)

In [76]:
(require racket/trace)

In [77]:
(trace my-append)

In [78]:
(my-append '(1 2 3) '(4 5 6))

>(my-append '(1 2 3) '(4 5 6))
> (my-append '(2 3) '(4 5 6))
> >(my-append '(3) '(4 5 6))
> > (my-append '() '(4 5 6))
< < '(4 5 6)
< <'(3 4 5 6)
< '(2 3 4 5 6)
<'(1 2 3 4 5 6)


'(1 2 3 4 5 6)

We define <tt>replicate</tt> which creates n copies of an object in a list.

In [79]:
(define (replicate obj n)
  (if (zero? n)
      empty   ;; '()
      (cons obj (replicate obj (- n 1)))))

In [80]:
(replicate 'x 10)

'(x x x x x x x x x x)

In [81]:
(replicate 'hi 5)

'(hi hi hi hi hi)

In [82]:
(replicate '(1 2 3) 3)

'((1 2 3) (1 2 3) (1 2 3))

### Tail Recursion

Both <tt>my-append</tt> and <tt>replicate</tt> are <b>recursive</b>.  We note that both 
have to wait for the return of the recursive call before returning a final value.
Since recursion is normally implemented by pushing recursive calls onto a memory stack, these recursive calls can consume lots of resources.  

Guy Steele and Gerry Sussman of MIT in the 1970's noted that there is a way to avoid the overhead of the recursive calls piling up on the stack using <b>tail recursion</b>.  The idea is simple and elegant.  You write the procedure so that the last call in the function is the recursive call.  That way, there is no need to wait around for the result.

In [83]:
(require racket/trace)

In [84]:
(trace replicate)

In [86]:
(replicate 'x 10)

>(replicate 'x 10)
> (replicate 'x 9)
> >(replicate 'x 8)
> > (replicate 'x 7)
> > >(replicate 'x 6)
> > > (replicate 'x 5)
> > > >(replicate 'x 4)
> > > > (replicate 'x 3)
> > > > >(replicate 'x 2)
> > > > > (replicate 'x 1)
> > > >[10] (replicate 'x 0)
< < < <[10] '()
< < < < < '(x)
< < < < <'(x x)
< < < < '(x x x)
< < < <'(x x x x)
< < < '(x x x x x)
< < <'(x x x x x x)
< < '(x x x x x x x)
< <'(x x x x x x x x)
< '(x x x x x x x x x)
<'(x x x x x x x x x x)


'(x x x x x x x x x x)

The nested calls to <tt>replicate</tt> indicate the number of items sitting on the stack.

We can define a tail recursive version of <tt>replicate</tt> for comparison

In [87]:
(define (trreplicate obj n)
  (trrepaux obj n empty))

(define (trrepaux obj n result)
  (if (zero? n)
      result
      (trrepaux obj (- n 1) (cons obj result))))

In [88]:
(trreplicate 'x 10)

'(x x x x x x x x x x)

In [89]:
(trace trreplicate)

In [90]:
(trreplicate 'x 10)

>(trreplicate 'x 10)
<'(x x x x x x x x x x)


'(x x x x x x x x x x)

We need to trace the helper function <tt>trrepaux</tt>

In [91]:
(trace trrepaux)

In [92]:
(trreplicate 'x 10)

>(trreplicate 'x 10)
>(trrepaux 'x 10 '())
>(trrepaux 'x 9 '(x))
>(trrepaux 'x 8 '(x x))
>(trrepaux 'x 7 '(x x x))
>(trrepaux 'x 6 '(x x x x))
>(trrepaux 'x 5 '(x x x x x))
>(trrepaux 'x 4 '(x x x x x x))
>(trrepaux 'x 3 '(x x x x x x x))
>(trrepaux 'x 2 '(x x x x x x x x))
>(trrepaux 'x 1 '(x x x x x x x x x))
>(trrepaux 'x 0 '(x x x x x x x x x x))
<'(x x x x x x x x x x)


'(x x x x x x x x x x)

Each call to <tt>trrepaux</tt> is independent.  They do not have to leave calls on the stack.

We can redefine <tt>trreplicate</tt> using the optional parameter and avoid the helper function.

In [93]:
(define (trreplicate2 obj n [result empty])
  (if (zero? n)
      result
      (trreplicate2 obj (- n 1) (cons obj result))))

In [94]:
(trreplicate2 'x 3)

'(x x x)

In [95]:
(trace trreplicate2)

In [96]:
(trreplicate2 'x 3)

>(trreplicate2 'x 3)
>(trreplicate2 'x 2 '(x))
>(trreplicate2 'x 1 '(x x))
>(trreplicate2 'x 0 '(x x x))
<'(x x x)


'(x x x)

We can create tail recursive versions of familiar functions such as 
- <tt>length</tt>
- <tt>sum</tt>
- <tt>max</tt>
- <tt>power</tt> Racket has the <tt>expt</tt> function.

both with and without helper functions.

In [97]:
(define (length lst)
  (if (null? lst) 0
      (+ 1 (length (cdr lst)))))

(define (trlength lst)
  (trlength-aux lst 0))

(define (trlength-aux lst length)
  (if (null? lst)
      length
      (trlength-aux (cdr lst) (+ 1 length))))

(define (trlength2 lst [length 0])
  (if (null? lst)
      length
      (trlength2 (cdr lst) (+ 1 length))))

In [98]:
(length '(a b c d e f g))

7

In [99]:
(trlength '(a b c d e f g))

7

In [100]:
(trlength2 '(a b c d e f g))

7

In [101]:
(define (sum lst)
  (if (null? lst) 0
      (+ (car lst) (sum (cdr lst)))))

(define (trsum lst)
  (trsum-aux lst 0))

(define (trsum-aux lst sum)
  (if (null? lst)
      sum
      (trsum-aux (cdr lst) (+ (car lst) sum))))

(define (trsum2 lst [sum 0])
  (if (null? lst)
      sum
      (trsum2 (cdr lst) (+ (car lst) sum))))

In [102]:
(sum '(2 4 6 8))

20

In [103]:
(trsum '(2 4 6 8))

20

In [104]:
(trsum2 '(2 4 6 8))

20

In racket, <tt>-inf.0</tt> is negative infinity as a real.

In [105]:
(integer? -inf.0)

#f

In [63]:
(real? -inf.0)

#t

In [106]:
(define (max lst)
  (if (null? lst)
      -inf.0
      (if (> (car lst) (max (cdr lst)))
        (car lst)
        (max (cdr lst)))))

(define (trmax lst)
  (trmax-aux lst -inf.0))

(define (trmax-aux lst max)
  (if (null? lst)
      max
      (if (> (car lst) max)
        (trmax-aux (cdr lst) (car lst))
        (trmax-aux (cdr lst) max))))

(define (trmax2 lst [max -inf.0])
  (if (null? lst)
      max
      (if (> (car lst) max)
        (trmax2 (cdr lst) (car lst))
        (trmax2 (cdr lst) max))))

In [107]:
(max '(-3 3 33 0))

max: contract violation
  expected: real?
  given: '(3 33 0)


In [108]:
(trmax '(-3 3 33 0))

33

In [109]:
(trmax2 '(-3 3 33 0))

33

In [110]:
(define (power x n)
  (if (zero? n)
      1
      (* x (power x (- n 1)))))

(define (trpower x n)
  (trpower-aux x n 1))

(define (trpower-aux x n result)
  (if (zero? n)
      result
      (trpower-aux x (- n 1) (* x result))))

(define (trpower2 x n [result 1])
  (if (zero? n)
      result
      (trpower2 x (- n 1) (* x result))))

In [111]:
(power 2 10)

1024

In [112]:
(trpower 2 10)

1024

In [113]:
(trpower2 2 10)

1024

### Even more power.

There is a faster algorithm for exponentiation.  See page 48 of <i>The Algorithm Design Manual</i> by Skienna.  <a target=wer href="https://link.springer.com/content/pdf/10.1007%2F978-1-84800-070-4.pdf">pdf</a>

It is faster than <tt>expt</tt>

In [114]:
(define (lgpower a n)
  (if (zero? n)
      1
      (let ((x (lgpower a (quotient n 2))))
    (if (even? n)
        (* x x)
        (* a x x)))))

In [115]:
(lgpower 2 10)

1024

In [116]:
(lgpower 2 100)

1267650600228229401496703205376

<b>Exercise:</b> Rewrite the <code>my-append</code> function as a tail-recursive function.

### Ackermann Function

See (https://en.wikipedia.org/wiki/Ackermann_function)

Ackermann was an interesting guy.  He gave up his career for love, or at least marriage.  Guy Steele had a similar shadow on his career.

In [117]:
(define (ack m n)
  (cond ((= m 0) (+ n 1))
    ((= n 0) (ack (- m 1) 1))  ;; m > 0
    (else
     (ack (- m 1) (ack m (- n 1))))))

In [118]:
(ack 2 2)

7

In [119]:
(trace ack)

In [120]:
(ack 2 2)

>(ack 2 2)
> (ack 2 1)
> >(ack 2 0)
> >(ack 1 1)
> > (ack 1 0)
> > (ack 0 1)
< < 2
> >(ack 0 2)
< <3
> (ack 1 3)
> >(ack 1 2)
> > (ack 1 1)
> > >(ack 1 0)
> > >(ack 0 1)
< < <2
> > (ack 0 2)
< < 3
> >(ack 0 3)
< <4
> (ack 0 4)
< 5
>(ack 1 5)
> (ack 1 4)
> >(ack 1 3)
> > (ack 1 2)
> > >(ack 1 1)
> > > (ack 1 0)
> > > (ack 0 1)
< < < 2
> > >(ack 0 2)
< < <3
> > (ack 0 3)
< < 4
> >(ack 0 4)
< <5
> (ack 0 5)
< 6
>(ack 0 6)
<7


7

Now we will memoize ack to avoid repetitive computations.

In [121]:
(define (ack m n)
  (cond ((= m 0) (+ n 1))
    ((= n 0) (ack (- m 1) 1))  ;; m > 0
    (else
     (ack (- m 1) (ack m (- n 1))))))

(define (memoize func [table (make-hash)])
  (lambda (arg1 arg2)
    (cond ((hash-has-key? table (list arg1 arg2))
       (begin
         (display (list 'used-hash arg1 arg2))
         (newline)
         (hash-ref table (list arg1 arg2))))
      (else
       (hash-set! table (list arg1 arg2) (func arg1 arg2))
       (hash-ref table (list arg1 arg2))))))

In [122]:
(define ack (memoize ack))

In [123]:
(ack 2 2)

(used-hash 1 1)
(used-hash 1 3)


7

In [124]:
(trace ack)

In [125]:
(ack 3 3)

>(ack 3 3)
> (ack 3 2)
> >(ack 3 1)
> > (ack 3 0)
> > >(ack 2 1)
(used-hash 2 1)
< < <5
< < 5
> > (ack 2 5)
> > >(ack 2 4)
> > > (ack 2 3)
> > > >(ack 2 2)
(used-hash 2 2)
< < < <7
> > > >(ack 1 7)
> > > > (ack 1 6)
> > > > >(ack 1 5)
(used-hash 1 5)
< < < < <7
> > > > >(ack 0 7)
< < < < <8
< < < < 8
> > > > (ack 0 8)
< < < < 9
< < < <9
< < < 9
> > > (ack 1 9)
> > > >(ack 1 8)
> > > > (ack 1 7)
(used-hash 1 7)
< < < < 9
> > > > (ack 0 9)
< < < < 10
< < < <10
> > > >(ack 0 10)
< < < <11
< < < 11
< < <11
> > >(ack 1 11)
> > > (ack 1 10)
> > > >(ack 1 9)
(used-hash 1 9)
< < < <11
> > > >(ack 0 11)
< < < <12
< < < 12
> > > (ack 0 12)
< < < 13
< < <13
< < 13
< <13
> >(ack 2 13)
> > (ack 2 12)
> > >(ack 2 11)
> > > (ack 2 10)
> > > >(ack 2 9)
> > > > (ack 2 8)
> > > > >(ack 2 7)
> > > > > (ack 2 6)
> > > >[10] (ack 2 5)
(used-hash 2 5)
< < < <[10] 13
> > > >[10] (ack 1 13)
> > > >[11] (ack 1 12)
> > > >[12] (ack 1 11)
(used-hash 1 11)
< < < <[12] 13
> > > >[12] (ack 0 13)
< < < <[12] 14
< < 

61

In [126]:
(ack 3 3)

>(ack 3 3)
(used-hash 3 3)
<61


61

In [127]:
(ack 2 2)

>(ack 2 2)
(used-hash 2 2)
<7


7